In [ ]:
# ..... build coexp nets? ..... #

In [2]:
library(SingleCellExperiment)
library(SummarizedExperiment)
library(scater)
library(Seurat)
library(dplyr)
library(scran)

In [3]:
## create bulk samples from cluster-specific sc data ##
get_bulk_samples <- function(mat, number_of_samples){
    nsamples = round(dim(mat)[2]/number_of_samples)    # divide into samples of ~20 cells each
    bulk_samples = matrix(NA, nrow = dim(mat)[1], ncol = nsamples)
    
    if(nsamples==1){
        bulk_samples[,1] = rowSums(mat)
    }else{
        for(ii in 1:(nsamples-1)){      
            ids = sample(dim(mat)[2], number_of_samples, replace = FALSE)
            bulk_samples[,ii] = rowSums(mat[,ids])
            mat <- mat[,-ids]        
        }
    }
    bulk_samples[,nsamples] = rowSums(mat)    
    rownames(bulk_samples) = rownames(mat)
    return(bulk_samples)
}

## create coexpression network ## 
build_coexp_network <- function(net, method = "spearman", flag = "rank"){
    
    # Calculate correlation coefficients
    genes = rownames(net)
    net = net[rowSums(net) > 0, ]

#     print(paste0("... ",dim(net)[1]," of ",length(genes), " genes have non-zero expression" ))

    net = cor(t(net), method = method)
    
    # Create network
    temp = net[upper.tri(net, diag = T)]
    if (flag == "abs"){
        temp = abs(temp)
    }
    
#     print("...ranking")
    temp = rank(temp, ties.method = "average")  

#     print("...reconstructing matrix")
    net[upper.tri(net, diag = T)] = temp

    net = t(net)
    net[upper.tri(net, diag = T)] = temp

    net = net / max(net, na.rm = T)
    med = median(net, na.rm = T)

    ind = setdiff(genes, rownames(net))   # which genes are missing?

    temp = matrix(med, length(ind), dim(net)[2])
    rownames(temp) = ind

    net = rbind(net, temp)
    temp = matrix(med, dim(net)[1], length(ind))
    colnames(temp) = ind
    net = cbind(net, temp)

    # reorder to original
    net = net[genes, genes]
    diag(net) = 1

    return(net)
}

# rank-standardize
get_rankstd <- function(aggNet){
    temp = aggNet[upper.tri(aggNet, diag = T)]
    temp = rank(temp, ties.method = "average")  
    aggNet[upper.tri(aggNet, diag = T)] = temp
    aggNet = t(aggNet)
    aggNet[upper.tri(aggNet, diag = T)] = temp
    aggNet = aggNet / max(aggNet, na.rm = T)
    return(aggNet)
}

In [34]:
# load individual sample files
sc1 = readRDS('human_Cao_data.rds')
# sc1 = readRDS('zebrafish_24hpf_Cao_data.rds')
# sc1 = readRDS('wfrog_24hpf_Cao_data.rds')

In [51]:
# load mouse data
load('~/septation/Qiu_mouse_E11.5.Rdata')
sc1 = sce2

sc1$celltype = sc1$major_trajectory

In [52]:
sc1@meta.data[1,]

ERROR: Error in eval(expr, envir, enclos): no slot of name "meta.data" for this object of class "SingleCellExperiment"


In [53]:
# SCE object
# sce = SingleCellExperiment(list(counts = sc1@assays$RNA@counts), colData = DataFrame(sc1@meta.data))
sce = sc1 # mouse
sce <- logNormCounts(sce)

In [54]:
hvgs <- getTopHVGs(sce, n = 6000)
length(hvgs)

[1] 6000

In [55]:
# threshold to top 4k genes expressed in at least 25k cells
sce <- sce[hvgs,]
dim(sce)

[1]   6000 233843

In [56]:
cpm(sce) <- calculateCPM(sce)

In [57]:
# build bulk samples, and coexp networks from bulk samples
cls_groups = unique(sce$celltype)
pb = txtProgressBar(min = 0, max = length(cls_groups), initial = 0)

full_bulk = c()

for(oo in 1:length(cls_groups)){

    currcls = cls_groups[oo]
    smp_id = which(sce$celltype==currcls & !is.na(sce$celltype))
    temp1 = cpm(sce)[,smp_id]
    sample_size = 20

    if(length(smp_id) >= sample_size){
        bulk1 = get_bulk_samples(temp1, sample_size)

        bulk1 = data.frame(bulk1)
        if(!length(full_bulk)){
            full_bulk = bulk1
        }else{
            full_bulk = cbind(full_bulk, bulk1)
        }
    }    
        
    setTxtProgressBar(pb, oo)
}

aggNet = build_coexp_network(full_bulk, method = 'spearman')

# save
fileo = paste0('mouse', '_sample_aggregate_top6000.Rdata')
save(aggNet, file = fileo)

In [58]:
aggNet[100:103,100:103]

Sorbs2      Mdga2      Tenm4      Pdzrn3     
Sorbs2 1.000000000 0.98250511 0.04687172 0.004937556
Mdga2  0.982505111 1.00000000 0.14023239 0.052124278
Tenm4  0.046871722 0.14023239 1.00000000 0.990364444
Pdzrn3 0.004937556 0.05212428 0.99036444 1.000000000